In [1]:
#
import pandas as pd
import numpy as np
from pandas.io.json import json_normalize
import os

In [2]:
import pandas as pd
import numpy as np
import pickle
from scipy import stats
import tensorflow as tf
import seaborn as sns
from pylab import rcParams
from sklearn.model_selection import train_test_split
from keras.models import Model, load_model
from keras.layers import Input, Dense
from keras.callbacks import ModelCheckpoint, TensorBoard
from keras import regularizers

from sklearn.preprocessing import StandardScaler, MinMaxScaler
from tensorflow.keras.layers import Input, Dense, Dropout
from tensorflow.keras.models import Model
from tensorflow.keras.optimizers import Adam, RMSprop
from tensorflow.keras.callbacks import EarlyStopping
import matplotlib.pyplot as plt
from sklearn.ensemble import IsolationForest



In [3]:
# /Users/wani/Desktop/
file_path = './datasets/'

In [4]:
dissoultion = pd.read_csv(file_path + 'dissolution_tank.csv', encoding='cp949')
dissoultion

STD_DT     NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP TAG
0        2020-03-04 0:00       0        489         116          631  3.19  OK
1        2020-03-04 0:00       1        433          78          609  3.19  OK
2        2020-03-04 0:00       2        464         154          608  3.19  OK
3        2020-03-04 0:00       3        379         212          606  3.19  OK
4        2020-03-04 0:00       4        798        1736          604  3.21  OK
...                  ...     ...        ...         ...          ...   ...  ..
835195  2020-04-30 23:59  835195        755        1743          318  3.21  OK
835196  2020-04-30 23:59  835196        385         206          317  3.19  OK
835197  2020-04-30 23:59  835197        465         148          316  3.20  OK
835198  2020-04-30 23:59  835198        467           0          314  3.19  OK
835199  2020-04-30 23:59  835199        453         125          312  3.20  OK

[835200 rows x 7 columns]

In [5]:
'''

1. 데이터 셋 -> 전처리 과정
* 과연 이상치 제거 해야하는가? -> EDA 분석에서 놓쳤던 점들을 판단해보자!
    ** INSP 분포 / 각 컬럼별 분포가 어떻게 되어있는지 파악하기 / EDA 분석 ->  분포별 구획을 정해서 해당 내 있는 데이터 셋 확인
2. 가능하다면, 시간별로 데이터가 어떻게 구성되어 있는지, //
3. 전처리 scaler mixmin / z-score로 할것인지 판단하기 
'''

'\n\n1. 데이터 셋 -> 전처리 과정\n* 과연 이상치 제거 해야하는가? -> EDA 분석에서 놓쳤던 점들을 판단해보자!\n    ** INSP 분포 / 각 컬럼별 분포가 어떻게 되어있는지 파악하기 / EDA 분석 ->  분포별 구획을 정해서 해당 내 있는 데이터 셋 확인\n2. 가능하다면, 시간별로 데이터가 어떻게 구성되어 있는지, //\n3. 전처리 scaler mixmin / z-score로 할것인지 판단하기 \n'

In [6]:
dissoul = dissoultion.copy()
dissoul

STD_DT     NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP TAG
0        2020-03-04 0:00       0        489         116          631  3.19  OK
1        2020-03-04 0:00       1        433          78          609  3.19  OK
2        2020-03-04 0:00       2        464         154          608  3.19  OK
3        2020-03-04 0:00       3        379         212          606  3.19  OK
4        2020-03-04 0:00       4        798        1736          604  3.21  OK
...                  ...     ...        ...         ...          ...   ...  ..
835195  2020-04-30 23:59  835195        755        1743          318  3.21  OK
835196  2020-04-30 23:59  835196        385         206          317  3.19  OK
835197  2020-04-30 23:59  835197        465         148          316  3.20  OK
835198  2020-04-30 23:59  835198        467           0          314  3.19  OK
835199  2020-04-30 23:59  835199        453         125          312  3.20  OK

[835200 rows x 7 columns]

In [7]:
dissoultion.corr(method='pearson') 


NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT      INSP
NUM          1.000000   0.000188   -0.000050     0.080079 -0.000524
MELT_TEMP    0.000188   1.000000    0.944929    -0.000336  0.916295
MOTORSPEED  -0.000050   0.944929    1.000000     0.000123  0.887813
MELT_WEIGHT  0.080079  -0.000336    0.000123     1.000000 -0.000005
INSP        -0.000524   0.916295    0.887813    -0.000005  1.000000

In [8]:
#replace(24, 100)
dissoul = dissoul.replace('OK', 0) # 정상 OK 0, 불량 NG 1 //
dissoul = dissoul.replace('NG', 1)
dissoul # 시간별 데이터 구성 살펴볼까요? EDA 

# 데이터 라벨링 ex) NG, OK  -> 1(N), 0(OK)

STD_DT     NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  \
0        2020-03-04 0:00       0        489         116          631  3.19   
1        2020-03-04 0:00       1        433          78          609  3.19   
2        2020-03-04 0:00       2        464         154          608  3.19   
3        2020-03-04 0:00       3        379         212          606  3.19   
4        2020-03-04 0:00       4        798        1736          604  3.21   
...                  ...     ...        ...         ...          ...   ...   
835195  2020-04-30 23:59  835195        755        1743          318  3.21   
835196  2020-04-30 23:59  835196        385         206          317  3.19   
835197  2020-04-30 23:59  835197        465         148          316  3.20   
835198  2020-04-30 23:59  835198        467           0          314  3.19   
835199  2020-04-30 23:59  835199        453         125          312  3.20   

        TAG  
0         0  
1         0  
2         0  
3         0  
4         0  
...     ...  
835195    0  
835196    0  
835197    0  
835198    0  
835199    0  

[835200 rows x 7 columns]

In [9]:
OK_dissoul = dissoul[dissoul['TAG'] == 0] #정상 
NG_dissoul = dissoul[dissoul['TAG'] == 1] #비정상
# 3.04 0:00 - 4.30 23:59 기간 

In [10]:
#dissoul.query('"0:00"<= STD_DT <= "0:59"')
len(dissoul[dissoul['STD_DT'].str.contains('2020-03-04 0:02')]) # 1초마다 10개의 데이터 씩 존재함
# 10개의 데이터가 있지만, curving shift를 지나면서 1개를 빼고 9개만 처리 해주면 된다라고 판단함.
# 우리는 고민해봐야하는게 9개씩 끊어 있기 때문에 9개씩 묶어서 학습을 시겨야 함 / 그리고 다음 step에 넘어갈 때, 1분 뒤의 데이터를 예측한다면 60임
# 앞서 데이터 학습 시킬 때 / OK, NG만 부분적으로 나누고 학습을 시켜서 이상적인 데이터만 가지고 학습을 한다고 해서 
# 제대로 학습되지 않아 문제가 생김 - 정확도는 높아져도,  prediction 정반대로 이루어짐 
# case 1. 1초단위 9개씩 묶어서 학습을 시키고 (이상 / 정상 데이터 고려하지 않음) case2. 정상 데이터만 / 비정상 나누어 데이터 학습 
# case 3. 1초마다 단위의 정상 데이터를 가지고 학습하기 (컬)

# 1분단위로 나누어져 있는 1분 전에, 예측을 할려면  10개 데이터 먼저 예측해야함 ( 만약 1분전 데이터를 예측하려면 10*60 = 600 )
# curving shift로 먼저 예측 후 / 본래 NG 데이터 제거 

# 1초당 9개 데이터 안 OK / NG 몇 개 있는지 판단하기 
# 3/04 ~ 3/16 까지 , 4/15 ~ 4/30까지를 제외할 것인가? 분석을 어떻게 하냐에 따라 다를 것임...
# 1 day 단위로 된다면 우리는 15일을 예측해서 고장을 판단해야 하지 않을까?



10

In [ ]:
# 데이터를 차원 축소생각은??
# 1. scaling 진행해야 한다.
# 2. 각각의 시간별로 데이터 10개 차원 축소로 추출한다.


In [51]:
dissoul

STD_DT     NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  \
0        2020-03-04 0:00       0        489         116          631  3.19   
1        2020-03-04 0:00       1        433          78          609  3.19   
2        2020-03-04 0:00       2        464         154          608  3.19   
3        2020-03-04 0:00       3        379         212          606  3.19   
4        2020-03-04 0:00       4        798        1736          604  3.21   
...                  ...     ...        ...         ...          ...   ...   
835195  2020-04-30 23:59  835195        755        1743          318  3.21   
835196  2020-04-30 23:59  835196        385         206          317  3.19   
835197  2020-04-30 23:59  835197        465         148          316  3.20   
835198  2020-04-30 23:59  835198        467           0          314  3.19   
835199  2020-04-30 23:59  835199        453         125          312  3.20   

        TAG  
0         0  
1         0  
2         0  
3         0  
4         0  
...     ...  
835195    0  
835196    0  
835197    0  
835198    0  
835199    0  

[835200 rows x 7 columns]

In [53]:
s = dissoul[dissoul['STD_DT'].str.contains('2020-03-04 0:05')]
s = s[['MELT_TEMP', 'MOTORSPEED', 'MELT_WEIGHT',
                         'INSP']]

# 독립변수
#dissoul_x = dissoul[['MELT_TEMP', 'MOTORSPEED', 'MELT_WEIGHT',
#                         'INSP']]
#dissoul_y = dissoul[['TAG']]
s

MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP
50        440         107          537  3.19
51        432          76          536  3.19
52        468         171          534  3.19
53        405         216          532  3.19
54        797        1739          531  3.21
55        752        1723          530  3.22
56        398         205          528  3.18
57        478         148          526  3.19
58        449          76          525  3.19
59        497         152          523  3.19

In [55]:
from sklearn.decomposition import PCA

s_scaled = StandardScaler().fit_transform(s.values)

array([[-0.53053283, -0.55667348,  1.52204904, -0.3592106 ],
       [-0.58981024, -0.60538045,  1.2982183 , -0.3592106 ],
       [-0.32306189, -0.45611716,  0.85055681, -0.3592106 ],
       [-0.7898715 , -0.3854135 ,  0.40289533, -0.3592106 ],
       [ 2.11472164,  2.00751257,  0.17906459,  1.43684242],
       [ 1.78128621,  1.9823735 , -0.04476615,  2.33486893],
       [-0.84173924, -0.40269662, -0.49242763, -1.25723711],
       [-0.24896513, -0.49225459, -0.94008911, -0.3592106 ],
       [-0.46384574, -0.60538045, -1.16391985, -0.3592106 ],
       [-0.10818128, -0.48596982, -1.61158133, -0.3592106 ]])

In [56]:
s_scaled.shape

(10, 4)

In [11]:
# 데이터 날짜별로 검색하기 ---

def datatimeFind(data, target, time):
    
    
    find = data[data[target].str.contains(time)]
    
    return find

In [12]:
datatimeFind(dissoul, 'STD_DT', '2020-04-04 0:05')


STD_DT     NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  TAG
446450  2020-04-04 0:05  446450        483         130          154  3.19    0
446451  2020-04-04 0:05  446451        469          80          153  3.19    0
446452  2020-04-04 0:05  446452        494         165          152  3.19    0
446453  2020-04-04 0:05  446453        393         187          150  3.19    1
446454  2020-04-04 0:05  446454        754        1751          148  3.21    0
446455  2020-04-04 0:05  446455        739        1744          147  3.22    0
446456  2020-04-04 0:05  446456        410         189          145  3.18    1
446457  2020-04-04 0:05  446457        499         163          144  3.19    0
446458  2020-04-04 0:05  446458        447           0          142  3.19    1
446459  2020-04-04 0:05  446459        508         127          141  3.20    0

In [13]:
dissoul[dissoul['STD_DT'].str.contains('2020-03-04 0:05')]

STD_DT  NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  TAG
50  2020-03-04 0:05   50        440         107          537  3.19    0
51  2020-03-04 0:05   51        432          76          536  3.19    0
52  2020-03-04 0:05   52        468         171          534  3.19    0
53  2020-03-04 0:05   53        405         216          532  3.19    0
54  2020-03-04 0:05   54        797        1739          531  3.21    0
55  2020-03-04 0:05   55        752        1723          530  3.22    0
56  2020-03-04 0:05   56        398         205          528  3.18    0
57  2020-03-04 0:05   57        478         148          526  3.19    0
58  2020-03-04 0:05   58        449          76          525  3.19    0
59  2020-03-04 0:05   59        497         152          523  3.19    0

In [14]:
dissoul #이번에는 시간 1초당 버프를 하나씩 가져가도록 하기...
# 1초당 어떠한  feature extraction을 가지고 있는지 판단하기 위해서는 벡터 변환이 필요하다 / 먼저 각 초당

# 각 분당 10개의 데이터 평균을 내고 그에 따른 평균 이상의 값들만 추출할 수 도 있고, 
# 구간별로 조건을 주어서 구분

STD_DT     NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  \
0        2020-03-04 0:00       0        489         116          631  3.19   
1        2020-03-04 0:00       1        433          78          609  3.19   
2        2020-03-04 0:00       2        464         154          608  3.19   
3        2020-03-04 0:00       3        379         212          606  3.19   
4        2020-03-04 0:00       4        798        1736          604  3.21   
...                  ...     ...        ...         ...          ...   ...   
835195  2020-04-30 23:59  835195        755        1743          318  3.21   
835196  2020-04-30 23:59  835196        385         206          317  3.19   
835197  2020-04-30 23:59  835197        465         148          316  3.20   
835198  2020-04-30 23:59  835198        467           0          314  3.19   
835199  2020-04-30 23:59  835199        453         125          312  3.20   

        TAG  
0         0  
1         0  
2         0  
3         0  
4         0  
...     ...  
835195    0  
835196    0  
835197    0  
835198    0  
835199    0  

[835200 rows x 7 columns]

In [123]:
dissoul.mean() ##
#MELT_TEMP         509.200623
#MOTORSPEED        459.782865
#MELT_WEIGHT       582.962125
#INSP                3.194853

/var/folders/ts/qlqc0dr52sn_xpkshw60mrmr0000gn/T/ipykernel_63166/3644862372.py:1: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  dissoul.mean()


NUM            417599.500000
MELT_TEMP         509.200623
MOTORSPEED        459.782865
MELT_WEIGHT       582.962125
INSP                3.194853
TAG                 0.212006
dtype: float64

In [126]:
# 평균보다 큰 데이터 얼마나 되는지 확인해보는 것
dissoul[(dissoul['MELT_WEIGHT']>=582.962125) & (dissoul['MELT_TEMP']>=509.200623)]
#582.962125

STD_DT     NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  \
4        2020-03-04 0:00       4        798        1736          604  3.21   
5        2020-03-04 0:00       5        743        1722          603  3.21   
14       2020-03-04 0:01      14        740        1740          590  3.22   
15       2020-03-04 0:01      15        772        1729          588  3.22   
504      2020-03-04 0:50     504        748        1730          634  3.22   
...                  ...     ...        ...         ...          ...   ...   
834975  2020-04-30 23:37  834975        752        1763          615  3.21   
834984  2020-04-30 23:38  834984        799        1745          601  3.21   
834985  2020-04-30 23:38  834985        743        1760          600  3.22   
834994  2020-04-30 23:39  834994        746        1757          586  3.22   
834995  2020-04-30 23:39  834995        746        1733          585  3.22   

        TAG  
4         0  
5         0  
14        0  
15        0  
504       0  
...     ...  
834975    0  
834984    0  
834985    0  
834994    0  
834995    0  

[46636 rows x 7 columns]

In [124]:
#dissoul(dissoul['MELT_WEIGHT'])['aaa']
#pd.DataFrame(d[0])

0  1    2    3    4     5  6
0  2020-03-04 0:00  0  489  116  631  3.19  0

In [15]:
z = dissoul[dissoul['STD_DT'].str.contains('2020-03-04 0:05')]


In [16]:
z['MELT_TEMP'].median()

458.5

In [140]:
print(z['MELT_TEMP'].mean()) #
print(z['MOTORSPEED'].mean())
print(z['MELT_WEIGHT'].mean())
print(z['INSP'].mean())

511.6
461.3
530.2
3.194


In [141]:
z[(z['MOTORSPEED']>=461.3) & (z['MELT_TEMP']>=511.6) & (z['MELT_WEIGHT']>=530.2) & (z['INSP']>=3.194)]

STD_DT  NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  TAG
54  2020-03-04 0:05   54        797        1739          531  3.21    0

In [138]:
z[z['MELT_TEMP'] >= z['MELT_TEMP'].mean()]

STD_DT  NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  TAG
54  2020-03-04 0:05   54        797        1739          531  3.21    0
55  2020-03-04 0:05   55        752        1723          530  3.22    0

In [150]:
z.columns[5]

'INSP'

In [165]:
len(z.columns)

7

In [17]:
# 모든 시간 데이터 리스트로 저장 
def timegetList(data, target):
    time_list = []
    
    for i in data[target]:
        if i not in time_list:
            time_list.append(i)
    print("===추출 완료===")
    return time_list

In [18]:
t = timegetList(dissoul, 'STD_DT')


===추출 완료===


In [19]:
t

['2020-03-04 0:00',
 '2020-03-04 0:01',
 '2020-03-04 0:02',
 '2020-03-04 0:03',
 '2020-03-04 0:04',
 '2020-03-04 0:05',
 '2020-03-04 0:06',
 '2020-03-04 0:07',
 '2020-03-04 0:08',
 '2020-03-04 0:09',
 '2020-03-04 0:10',
 '2020-03-04 0:11',
 '2020-03-04 0:12',
 '2020-03-04 0:13',
 '2020-03-04 0:14',
 '2020-03-04 0:15',
 '2020-03-04 0:16',
 '2020-03-04 0:17',
 '2020-03-04 0:18',
 '2020-03-04 0:19',
 '2020-03-04 0:20',
 '2020-03-04 0:21',
 '2020-03-04 0:22',
 '2020-03-04 0:23',
 '2020-03-04 0:24',
 '2020-03-04 0:25',
 '2020-03-04 0:26',
 '2020-03-04 0:27',
 '2020-03-04 0:28',
 '2020-03-04 0:29',
 '2020-03-04 0:30',
 '2020-03-04 0:31',
 '2020-03-04 0:32',
 '2020-03-04 0:33',
 '2020-03-04 0:34',
 '2020-03-04 0:35',
 '2020-03-04 0:36',
 '2020-03-04 0:37',
 '2020-03-04 0:38',
 '2020-03-04 0:39',
 '2020-03-04 0:40',
 '2020-03-04 0:41',
 '2020-03-04 0:42',
 '2020-03-04 0:43',
 '2020-03-04 0:44',
 '2020-03-04 0:45',
 '2020-03-04 0:46',
 '2020-03-04 0:47',
 '2020-03-04 0:48',
 '2020-03-04 0:49',


In [20]:
len(t)

83520

In [21]:
# 검색하여 원하는 날짜만 뽑아내기 
def getselectData10(data, column, time):
    selData = data.loc[[0]]
    l_sel = data[data[column].str.contains(time)]
    l_sel = l_sel[(l_sel[l_sel.columns[2]]>=l_sel[l_sel.columns[2]].mean()) & 
                  (l_sel[l_sel.columns[3]]>=l_sel[l_sel.columns[3]].mean()) & 
                  (l_sel[l_sel.columns[4]]>=l_sel[l_sel.columns[4]].mean()) & 
                  (l_sel[l_sel.columns[5]]>=l_sel[l_sel.columns[5]].mean())]
    selData = selData.append(l_sel, ignore_index = True)
    selData = selData.drop(0)
    return selData

In [22]:
getselectData10(dissoul, 'STD_DT', '2020-03-04 15:07')


STD_DT   NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  TAG
1  2020-03-04 15:07  9074        745        1777          275  3.22    0
2  2020-03-04 15:07  9075        741        1736          274  3.21    0

In [23]:
getselectData10(dissoul, 'STD_DT', '2020-03-04 20:01')


STD_DT    NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  TAG
1  2020-03-04 20:01  12014        746        1743          301  3.21    0

In [24]:
selD = dissoul.loc[[0]]
s = getselectData10(dissoul, 'STD_DT', '2020-03-04 20:10')
selD.append(s, ignore_index = True)

STD_DT    NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  TAG
0   2020-03-04 0:00      0        489         116          631  3.19    0
1  2020-03-04 20:10  12104        728        1712          175  3.21    0

In [212]:
'''
def allgetData10(data, column):
    selD = data.loc[[0]]
    #t = timegetList(dissoul, "STD_DT")
    for i in f:
        s = getselectData10(data, column, f)
        newD = selD.append(s, ignore_index = True)
    
    return newD
    
'''

In [40]:
test_time = ['2020-04-30 23:00', '2020-04-30 23:01', '2020-04-30 23:02', '2020-04-30 23:03',
            '2020-04-30 23:04', '2020-04-30 23:05', '2020-04-30 23:06', '2020-04-30 23:07']


In [41]:
for i in test_time:
    l = dissoul[dissoul["STD_DT"].str.contains(i)]
    #s = (l[l.columns[2]].median())
    #l[(l[l.columns[2]]>=l[l.columns[2]].mean())]
    l = l[(l[l.columns[2]]>=(l[l.columns[2]].median())) & (l[l.columns[3]]>=(l[l.columns[3]].median())) &
         (l[l.columns[4]]>=(l[l.columns[4]].median())) & (l[l.columns[5]]>=(l[l.columns[5]].median()))]
    print(l)
    

                  STD_DT     NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  \
834604  2020-04-30 23:00  834604        749        1757          330  3.21   

        TAG  
834604    0  
                  STD_DT     NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  \
834614  2020-04-30 23:01  834614        761        1736          316  3.22   

        TAG  
834614    0  
                  STD_DT     NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  \
834624  2020-04-30 23:02  834624        755        1735          298  3.21   

        TAG  
834624    0  
                  STD_DT     NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  \
834634  2020-04-30 23:03  834634        737        1736          282  3.21   

        TAG  
834634    0  
                  STD_DT     NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  \
834642  2020-04-30 23:04  834642        487         212          271  3.19   
834644  2020-04-30 23:04  834644        746        1717          268  3.21   

        TAG  
834642    0

In [76]:
sg = datatimeFind(dissoul, 'STD_DT', '2020-04-04 0:05')
sg.sample(n=1, axis = 0)

STD_DT     NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  TAG
446459  2020-04-04 0:05  446459        508         127          141   3.2    0

In [ ]:
def getTimeDataMedian(data, column):
    
    
    for i test_time:
        l = data[data[column].str.contains(i)]
            

In [ ]:
# 1. 각 컬럼의 중간 값을 찾아서 그에 맞는 행이 있는지 확인하고
# 2. 모든 시간별로 1분마다 10개의 샘플 데이터 중 분포도를 확인하여 유사값을 추출?? / 랜덤으로 1~ 10 까지 매 루프마다 1개씩 뽑아서 추출?

# 3. 10개 데이터 백터화 유사도 측정


In [45]:
import random
a = random.randint(0, 9)
print(a)

4


In [82]:
# 10개 중 임의 추출, 시간대별로 / 추출하여 새로운 데이터프레임 생성 -> 그룹별 샘플 추출 
def getTimeRandom(data, column):
    ddf = data.loc[[0]]
    for i in t:
        #l = data[data[column].str.contains(i)]
        l = datatimeFind(data, column, i)
        l = l.sample(n=1, axis = 0)
        ddf = ddf.append(l, ignore_index = True)
        
        # 출력해서 현재 상태확인 /
        print("======= "+i+" ======= "+"진행중...")
    ddf = ddf.drop(0)
    
    return ddf

In [83]:
ddfnew = getTimeRandom(dissoul, 'STD_DT')
ddfnew

======= 2020-03-04 0:00 ======= 진행중...
======= 2020-03-04 0:01 ======= 진행중...
======= 2020-03-04 0:02 ======= 진행중...
======= 2020-03-04 0:03 ======= 진행중...
======= 2020-03-04 0:04 ======= 진행중...
======= 2020-03-04 0:05 ======= 진행중...
======= 2020-03-04 0:06 ======= 진행중...
======= 2020-03-04 0:07 ======= 진행중...
======= 2020-03-04 0:08 ======= 진행중...
======= 2020-03-04 0:09 ======= 진행중...
======= 2020-03-04 0:10 ======= 진행중...
======= 2020-03-04 0:11 ======= 진행중...
======= 2020-03-04 0:12 ======= 진행중...
======= 2020-03-04 0:13 ======= 진행중...
======= 2020-03-04 0:14 ======= 진행중...
======= 2020-03-04 0:15 ======= 진행중...
======= 2020-03-04 0:16 ======= 진행중...
======= 2020-03-04 0:17 ======= 진행중...
======= 2020-03-04 0:18 ======= 진행중...
======= 2020-03-04 0:19 ======= 진행중...
======= 2020-03-04 0:20 ======= 진행중...
======= 2020-03-04 0:21 ======= 진행중...
======= 2020-03-04 0:22 ======= 진행중...
======= 2020-03-04 0:23 ======= 진행중...
======= 2020-03-04 0:24 ======= 진행중...
======= 2020-03-04 0:25 =

======= 2020-03-04 3:31 ======= 진행중...
======= 2020-03-04 3:32 ======= 진행중...
======= 2020-03-04 3:33 ======= 진행중...
======= 2020-03-04 3:34 ======= 진행중...
======= 2020-03-04 3:35 ======= 진행중...
======= 2020-03-04 3:36 ======= 진행중...
======= 2020-03-04 3:37 ======= 진행중...
======= 2020-03-04 3:38 ======= 진행중...
======= 2020-03-04 3:39 ======= 진행중...
======= 2020-03-04 3:40 ======= 진행중...
======= 2020-03-04 3:41 ======= 진행중...
======= 2020-03-04 3:42 ======= 진행중...
======= 2020-03-04 3:43 ======= 진행중...
======= 2020-03-04 3:44 ======= 진행중...
======= 2020-03-04 3:45 ======= 진행중...
======= 2020-03-04 3:46 ======= 진행중...
======= 2020-03-04 3:47 ======= 진행중...
======= 2020-03-04 3:48 ======= 진행중...
======= 2020-03-04 3:49 ======= 진행중...
======= 2020-03-04 3:50 ======= 진행중...
======= 2020-03-04 3:51 ======= 진행중...
======= 2020-03-04 3:52 ======= 진행중...
======= 2020-03-04 3:53 ======= 진행중...
======= 2020-03-04 3:54 ======= 진행중...
======= 2020-03-04 3:55 ======= 진행중...
======= 2020-03-04 3:56 =

======= 2020-03-04 7:02 ======= 진행중...
======= 2020-03-04 7:03 ======= 진행중...
======= 2020-03-04 7:04 ======= 진행중...
======= 2020-03-04 7:05 ======= 진행중...
======= 2020-03-04 7:06 ======= 진행중...
======= 2020-03-04 7:07 ======= 진행중...
======= 2020-03-04 7:08 ======= 진행중...
======= 2020-03-04 7:09 ======= 진행중...
======= 2020-03-04 7:10 ======= 진행중...
======= 2020-03-04 7:11 ======= 진행중...
======= 2020-03-04 7:12 ======= 진행중...
======= 2020-03-04 7:13 ======= 진행중...
======= 2020-03-04 7:14 ======= 진행중...
======= 2020-03-04 7:15 ======= 진행중...
======= 2020-03-04 7:16 ======= 진행중...
======= 2020-03-04 7:17 ======= 진행중...
======= 2020-03-04 7:18 ======= 진행중...
======= 2020-03-04 7:19 ======= 진행중...
======= 2020-03-04 7:20 ======= 진행중...
======= 2020-03-04 7:21 ======= 진행중...
======= 2020-03-04 7:22 ======= 진행중...
======= 2020-03-04 7:23 ======= 진행중...
======= 2020-03-04 7:24 ======= 진행중...
======= 2020-03-04 7:25 ======= 진행중...
======= 2020-03-04 7:26 ======= 진행중...
======= 2020-03-04 7:27 =

======= 2020-03-04 10:32 ======= 진행중...
======= 2020-03-04 10:33 ======= 진행중...
======= 2020-03-04 10:34 ======= 진행중...
======= 2020-03-04 10:35 ======= 진행중...
======= 2020-03-04 10:36 ======= 진행중...
======= 2020-03-04 10:37 ======= 진행중...
======= 2020-03-04 10:38 ======= 진행중...
======= 2020-03-04 10:39 ======= 진행중...
======= 2020-03-04 10:40 ======= 진행중...
======= 2020-03-04 10:41 ======= 진행중...
======= 2020-03-04 10:42 ======= 진행중...
======= 2020-03-04 10:43 ======= 진행중...
======= 2020-03-04 10:44 ======= 진행중...
======= 2020-03-04 10:45 ======= 진행중...
======= 2020-03-04 10:46 ======= 진행중...
======= 2020-03-04 10:47 ======= 진행중...
======= 2020-03-04 10:48 ======= 진행중...
======= 2020-03-04 10:49 ======= 진행중...
======= 2020-03-04 10:50 ======= 진행중...
======= 2020-03-04 10:51 ======= 진행중...
======= 2020-03-04 10:52 ======= 진행중...
======= 2020-03-04 10:53 ======= 진행중...
======= 2020-03-04 10:54 ======= 진행중...
======= 2020-03-04 10:55 ======= 진행중...
======= 2020-03-04 10:56 ======= 진행중...


======= 2020-03-04 13:57 ======= 진행중...
======= 2020-03-04 13:58 ======= 진행중...
======= 2020-03-04 13:59 ======= 진행중...
======= 2020-03-04 14:00 ======= 진행중...
======= 2020-03-04 14:01 ======= 진행중...
======= 2020-03-04 14:02 ======= 진행중...
======= 2020-03-04 14:03 ======= 진행중...
======= 2020-03-04 14:04 ======= 진행중...
======= 2020-03-04 14:05 ======= 진행중...
======= 2020-03-04 14:06 ======= 진행중...
======= 2020-03-04 14:07 ======= 진행중...
======= 2020-03-04 14:08 ======= 진행중...
======= 2020-03-04 14:09 ======= 진행중...
======= 2020-03-04 14:10 ======= 진행중...
======= 2020-03-04 14:11 ======= 진행중...
======= 2020-03-04 14:12 ======= 진행중...
======= 2020-03-04 14:13 ======= 진행중...
======= 2020-03-04 14:14 ======= 진행중...
======= 2020-03-04 14:15 ======= 진행중...
======= 2020-03-04 14:16 ======= 진행중...
======= 2020-03-04 14:17 ======= 진행중...
======= 2020-03-04 14:18 ======= 진행중...
======= 2020-03-04 14:19 ======= 진행중...
======= 2020-03-04 14:20 ======= 진행중...
======= 2020-03-04 14:21 ======= 진행중...


...

======= 2020-04-30 11:36 ======= 진행중...
======= 2020-04-30 11:37 ======= 진행중...
======= 2020-04-30 11:38 ======= 진행중...
======= 2020-04-30 11:39 ======= 진행중...
======= 2020-04-30 11:40 ======= 진행중...
======= 2020-04-30 11:41 ======= 진행중...
======= 2020-04-30 11:42 ======= 진행중...
======= 2020-04-30 11:43 ======= 진행중...
======= 2020-04-30 11:44 ======= 진행중...
======= 2020-04-30 11:45 ======= 진행중...
======= 2020-04-30 11:46 ======= 진행중...
======= 2020-04-30 11:47 ======= 진행중...
======= 2020-04-30 11:48 ======= 진행중...
======= 2020-04-30 11:49 ======= 진행중...
======= 2020-04-30 11:50 ======= 진행중...
======= 2020-04-30 11:51 ======= 진행중...
======= 2020-04-30 11:52 ======= 진행중...
======= 2020-04-30 11:53 ======= 진행중...
======= 2020-04-30 11:54 ======= 진행중...
======= 2020-04-30 11:55 ======= 진행중...
======= 2020-04-30 11:56 ======= 진행중...
======= 2020-04-30 11:57 ======= 진행중...
======= 2020-04-30 11:58 ======= 진행중...
======= 2020-04-30 11:59 ======= 진행중...
======= 2020-04-30 12:00 ======= 진행중...


======= 2020-04-30 15:01 ======= 진행중...
======= 2020-04-30 15:02 ======= 진행중...
======= 2020-04-30 15:03 ======= 진행중...
======= 2020-04-30 15:04 ======= 진행중...
======= 2020-04-30 15:05 ======= 진행중...
======= 2020-04-30 15:06 ======= 진행중...
======= 2020-04-30 15:07 ======= 진행중...
======= 2020-04-30 15:08 ======= 진행중...
======= 2020-04-30 15:09 ======= 진행중...
======= 2020-04-30 15:10 ======= 진행중...
======= 2020-04-30 15:11 ======= 진행중...
======= 2020-04-30 15:12 ======= 진행중...
======= 2020-04-30 15:13 ======= 진행중...
======= 2020-04-30 15:14 ======= 진행중...
======= 2020-04-30 15:15 ======= 진행중...
======= 2020-04-30 15:16 ======= 진행중...
======= 2020-04-30 15:17 ======= 진행중...
======= 2020-04-30 15:18 ======= 진행중...
======= 2020-04-30 15:19 ======= 진행중...
======= 2020-04-30 15:20 ======= 진행중...
======= 2020-04-30 15:21 ======= 진행중...
======= 2020-04-30 15:22 ======= 진행중...
======= 2020-04-30 15:23 ======= 진행중...
======= 2020-04-30 15:24 ======= 진행중...
======= 2020-04-30 15:25 ======= 진행중...


======= 2020-04-30 18:26 ======= 진행중...
======= 2020-04-30 18:27 ======= 진행중...
======= 2020-04-30 18:28 ======= 진행중...
======= 2020-04-30 18:29 ======= 진행중...
======= 2020-04-30 18:30 ======= 진행중...
======= 2020-04-30 18:31 ======= 진행중...
======= 2020-04-30 18:32 ======= 진행중...
======= 2020-04-30 18:33 ======= 진행중...
======= 2020-04-30 18:34 ======= 진행중...
======= 2020-04-30 18:35 ======= 진행중...
======= 2020-04-30 18:36 ======= 진행중...
======= 2020-04-30 18:37 ======= 진행중...
======= 2020-04-30 18:38 ======= 진행중...
======= 2020-04-30 18:39 ======= 진행중...
======= 2020-04-30 18:40 ======= 진행중...
======= 2020-04-30 18:41 ======= 진행중...
======= 2020-04-30 18:42 ======= 진행중...
======= 2020-04-30 18:43 ======= 진행중...
======= 2020-04-30 18:44 ======= 진행중...
======= 2020-04-30 18:45 ======= 진행중...
======= 2020-04-30 18:46 ======= 진행중...
======= 2020-04-30 18:47 ======= 진행중...
======= 2020-04-30 18:48 ======= 진행중...
======= 2020-04-30 18:49 ======= 진행중...
======= 2020-04-30 18:50 ======= 진행중...


======= 2020-04-30 21:51 ======= 진행중...
======= 2020-04-30 21:52 ======= 진행중...
======= 2020-04-30 21:53 ======= 진행중...
======= 2020-04-30 21:54 ======= 진행중...
======= 2020-04-30 21:55 ======= 진행중...
======= 2020-04-30 21:56 ======= 진행중...
======= 2020-04-30 21:57 ======= 진행중...
======= 2020-04-30 21:58 ======= 진행중...
======= 2020-04-30 21:59 ======= 진행중...
======= 2020-04-30 22:00 ======= 진행중...
======= 2020-04-30 22:01 ======= 진행중...
======= 2020-04-30 22:02 ======= 진행중...
======= 2020-04-30 22:03 ======= 진행중...
======= 2020-04-30 22:04 ======= 진행중...
======= 2020-04-30 22:05 ======= 진행중...
======= 2020-04-30 22:06 ======= 진행중...
======= 2020-04-30 22:07 ======= 진행중...
======= 2020-04-30 22:08 ======= 진행중...
======= 2020-04-30 22:09 ======= 진행중...
======= 2020-04-30 22:10 ======= 진행중...
======= 2020-04-30 22:11 ======= 진행중...
======= 2020-04-30 22:12 ======= 진행중...
======= 2020-04-30 22:13 ======= 진행중...
======= 2020-04-30 22:14 ======= 진행중...
======= 2020-04-30 22:15 ======= 진행중...


STD_DT     NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  TAG
1       2020-03-04 0:00       1        433          78          609  3.19    0
2       2020-03-04 0:01      15        772        1729          588  3.22    0
3       2020-03-04 0:02      27        483         167          571  3.19    0
4       2020-03-04 0:03      33        364         232          562  3.18    0
5       2020-03-04 0:04      46        402         203          543  3.18    0
...                 ...     ...        ...         ...          ...   ...  ...
83516  2020-04-30 23:55  835154        740        1748          373  3.22    0
83517  2020-04-30 23:56  835164        760        1725          355  3.21    0
83518  2020-04-30 23:57  835175        759        1723          342  3.22    0
83519  2020-04-30 23:58  835181        443          75          334  3.19    0
83520  2020-04-30 23:59  835190        497         141          323  3.20    0

[83520 rows x 7 columns]

In [84]:
ddfnew.to_csv("10dissoulsample.csv")



In [85]:
ddfnew = pd.read_csv('10dissoulsample.csv', encoding='cp949')  #
ddfnew

Unnamed: 0            STD_DT     NUM  MELT_TEMP  MOTORSPEED  \
0               1   2020-03-04 0:00       1        433          78   
1               2   2020-03-04 0:01      15        772        1729   
2               3   2020-03-04 0:02      27        483         167   
3               4   2020-03-04 0:03      33        364         232   
4               5   2020-03-04 0:04      46        402         203   
...           ...               ...     ...        ...         ...   
83515       83516  2020-04-30 23:55  835154        740        1748   
83516       83517  2020-04-30 23:56  835164        760        1725   
83517       83518  2020-04-30 23:57  835175        759        1723   
83518       83519  2020-04-30 23:58  835181        443          75   
83519       83520  2020-04-30 23:59  835190        497         141   

       MELT_WEIGHT  INSP  TAG  
0              609  3.19    0  
1              588  3.22    0  
2              571  3.19    0  
3              562  3.18    0  
4              543  3.18    0  
...            ...   ...  ...  
83515          373  3.22    0  
83516          355  3.21    0  
83517          342  3.22    0  
83518          334  3.19    0  
83519          323  3.20    0  

[83520 rows x 8 columns]

In [89]:
# # 비율을 살펴보자 - 원래 데이터 정상 / 비정상의 비율과 샘플 추출을 통한 전처리 후 데이터 비율은?? (알)
def ratioNormalData(data, target):
    # 정상 0
    normal = len(data[data[target] == 0])
    # 비정상 1
    abnormal = len(data[data[target] == 1])
    # 
    normal_ratio = (normal/(normal+abnormal))
    abnormal_ratio = (abnormal/(normal+abnormal))
    return normal_ratio, abnormal_ratio

In [90]:
ratioNormalData(dissoul, 'TAG') #정상 비정상 -원래 데이터

(0.7879944923371648, 0.21200550766283524)

In [91]:
ratioNormalData(ddfnew, 'TAG') # 샘플로 뽑은 추리면 데이터 똑같음 -> 전처리 표본 데이터 ㅍ추출 잘했음 / Stratified Random Sampling
# 그룹별 추출 임

(0.7899425287356322, 0.21005747126436783)

In [94]:
newdata = pd.read_csv('dissoulsample.csv', encoding='cp949')  #
newdata # 이거는 각 분당 맨 첫번쨰 데이터를 샘플 추출하였음.. 

Unnamed: 0           STD_DT     NUM  MELT_TEMP  MOTORSPEED  \
0               0    2020.3.4 0:00       0        489         116   
1               1    2020.3.4 0:01      10        507         128   
2               2    2020.3.4 0:02      20        474         135   
3               3    2020.3.4 0:03      30        437         129   
4               4    2020.3.4 0:04      40        450         145   
...           ...              ...     ...        ...         ...   
83515       83515  2020.4.30 23:55  835150        470         136   
83516       83516  2020.4.30 23:56  835160        496         103   
83517       83517  2020.4.30 23:57  835170        465         108   
83518       83518  2020.4.30 23:58  835180        498         133   
83519       83519  2020.4.30 23:59  835190        497         141   

       MELT_WEIGHT  INSP  TAG  
0              631  3.19    0  
1              596  3.19    0  
2              581  3.19    0  
3              567  3.19    0  
4              552  3.19    0  
...            ...   ...  ...  
83515          379  3.19    0  
83516          362  3.20    0  
83517          348  3.19    0  
83518          335  3.19    0  
83519          323  3.20    0  

[83520 rows x 8 columns]

In [97]:
meansample = pd.read_csv('datameansample.csv', encoding='cp949')  #
meansample


Unnamed: 0            STD_DT     NUM  MELT_TEMP  MOTORSPEED  \
0               1   2020-03-04 0:01      14        740        1740   
1               2   2020-03-04 0:02      24        740        1748   
2               3   2020-03-04 0:03      34        759        1718   
3               4   2020-03-04 0:04      44        757        1737   
4               5   2020-03-04 0:05      54        797        1739   
...           ...               ...     ...        ...         ...   
76313       76314  2020-04-30 23:54  835144        784        1751   
76314       76315  2020-04-30 23:55  835154        740        1748   
76315       76316  2020-04-30 23:57  835174        728        1737   
76316       76317  2020-04-30 23:58  835184        755        1715   
76317       76318  2020-04-30 23:59  835194        749        1740   

       MELT_WEIGHT  INSP  TAG  
0              590  3.22    0  
1              575  3.22    0  
2              560  3.21    0  
3              546  3.22    0  
4              531  3.21    0  
...            ...   ...  ...  
76313          387  3.22    0  
76314          373  3.22    0  
76315          344  3.21    0  
76316          330  3.22    0  
76317          319  3.21    0  

[76318 rows x 8 columns]

In [95]:

ratioNormalData(newdata, 'TAG') # 이거는 정상에 더 샘플이 치우쳐 있음 편향적 문제가 있음(ㅂ.... # Systematic Sampling



(0.849161877394636, 0.15083812260536397)

In [98]:
# meansample, 각 컬럼의 평균 이상의 데이터를 추출하였음. 그러나 ,
ratioNormalData(meansample, 'TAG') # 이거는 완전 샘플이 정상 데이터로 치우쳐 있음 -> 편향성 배제하지 못함 ... 
#?이유는 각 컬럼의 평균치를 뽑다 보니  -> 더욱 편향적으로 ㅊ데이터 추출에 어려움 / _편향성 

(1.0, 0.0)

In [99]:
ld = datatimeFind(dissoul, 'STD_DT', '2020-04-04 0:05')
ratioNormalData(ld, 'TAG')

(0.7, 0.3)

In [ ]:
# 다른 샘플링 방법 고려하여 그룹당 편향을 없애고 추출하는 방법, 
#  그럼 중간 값 처리하여 중간해당 행 추출 가능 각 시간그룹에서 그중간값 데이터 있으면 가져오고 없으면 그냥 두기?

In [ ]:
# ADASYN - 논문 참고 ( https://givitallugot.github.io/articles/2021-07/Python-imbalanced-sampling-copy)
'''
from imblearn.over_sampling import ADASYN

adasyn = ADASYN(random_state=22)
X_churn_ad, Y_churn_ad = adasyn.fit_resample(X_churn, Y_churn)
'''

In [225]:
# 10개의 데이터 실피기 위해 각 전  # 평균보다 높은 데이터를 뽑을 수 있고 그 평균 +1 -1 범위내에서 뽑을 수 있음
def getTimeData10(data, column):
    ddf = data.loc[[0]]
    #t = timegetList(dissoul, 'STD_DT')
    for i in t:
        l = data[data[column].str.contains(i)]
        l = l[(l[l.columns[2]]>=l[l.columns[2]].mean()) & (l[l.columns[3]]>=l[l.columns[3]].mean()) 
          & (l[l.columns[4]]>=l[l.columns[4]].mean()) & (l[l.columns[5]]>=l[l.columns[5]].mean())]
        
        ddf = ddf.append(l, ignore_index = True)
        print('========='+i+'작업 중...=========')
    ddf = ddf.drop(0)
    
    return ddf
        

In [226]:
dissoul.loc[[0]]


STD_DT  NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  TAG
0  2020-03-04 0:00    0        489         116          631  3.19    0

In [227]:
newdata = getTimeData10(dissoul, 'STD_DT')
newdata # 각 초마다 10개의 데이터 중 통계적 방법으로 평균 이상의 조건을 만들어서 최상의 조건을 찾아 새로운 데이터 생성
# 만약 이러한 통계적 방법이 처음부터 전처리 과정에서 이루어지지 않으면, 학습해도 의미 없는데이터로 특징 추출하지 않아 의미가 생성되지 않음


=========2020-03-04 0:00작업 중...=========
=========2020-03-04 0:01작업 중...=========
=========2020-03-04 0:02작업 중...=========
=========2020-03-04 0:03작업 중...=========
=========2020-03-04 0:04작업 중...=========
=========2020-03-04 0:05작업 중...=========
=========2020-03-04 0:06작업 중...=========
=========2020-03-04 0:07작업 중...=========
=========2020-03-04 0:08작업 중...=========
=========2020-03-04 0:09작업 중...=========
=========2020-03-04 0:10작업 중...=========
=========2020-03-04 0:11작업 중...=========
=========2020-03-04 0:12작업 중...=========
=========2020-03-04 0:13작업 중...=========
=========2020-03-04 0:14작업 중...=========
=========2020-03-04 0:15작업 중...=========
=========2020-03-04 0:16작업 중...=========
=========2020-03-04 0:17작업 중...=========
=========2020-03-04 0:18작업 중...=========
=========2020-03-04 0:19작업 중...=========
=========2020-03-04 0:20작업 중...=========
=========2020-03-04 0:21작업 중...=========
=========2020-03-04 0:22작업 중...=========
=========2020-03-04 0:23작업 중...=========
=========2020-03

=========2020-03-04 3:20작업 중...=========
=========2020-03-04 3:21작업 중...=========
=========2020-03-04 3:22작업 중...=========
=========2020-03-04 3:23작업 중...=========
=========2020-03-04 3:24작업 중...=========
=========2020-03-04 3:25작업 중...=========
=========2020-03-04 3:26작업 중...=========
=========2020-03-04 3:27작업 중...=========
=========2020-03-04 3:28작업 중...=========
=========2020-03-04 3:29작업 중...=========
=========2020-03-04 3:30작업 중...=========
=========2020-03-04 3:31작업 중...=========
=========2020-03-04 3:32작업 중...=========
=========2020-03-04 3:33작업 중...=========
=========2020-03-04 3:34작업 중...=========
=========2020-03-04 3:35작업 중...=========
=========2020-03-04 3:36작업 중...=========
=========2020-03-04 3:37작업 중...=========
=========2020-03-04 3:38작업 중...=========
=========2020-03-04 3:39작업 중...=========
=========2020-03-04 3:40작업 중...=========
=========2020-03-04 3:41작업 중...=========
=========2020-03-04 3:42작업 중...=========
=========2020-03-04 3:43작업 중...=========
=========2020-03

=========2020-03-04 6:40작업 중...=========
=========2020-03-04 6:41작업 중...=========
=========2020-03-04 6:42작업 중...=========
=========2020-03-04 6:43작업 중...=========
=========2020-03-04 6:44작업 중...=========
=========2020-03-04 6:45작업 중...=========
=========2020-03-04 6:46작업 중...=========
=========2020-03-04 6:47작업 중...=========
=========2020-03-04 6:48작업 중...=========
=========2020-03-04 6:49작업 중...=========
=========2020-03-04 6:50작업 중...=========
=========2020-03-04 6:51작업 중...=========
=========2020-03-04 6:52작업 중...=========
=========2020-03-04 6:53작업 중...=========
=========2020-03-04 6:54작업 중...=========
=========2020-03-04 6:55작업 중...=========
=========2020-03-04 6:56작업 중...=========
=========2020-03-04 6:57작업 중...=========
=========2020-03-04 6:58작업 중...=========
=========2020-03-04 6:59작업 중...=========
=========2020-03-04 7:00작업 중...=========
=========2020-03-04 7:01작업 중...=========
=========2020-03-04 7:02작업 중...=========
=========2020-03-04 7:03작업 중...=========
=========2020-03

=========2020-03-04 10:00작업 중...=========
=========2020-03-04 10:01작업 중...=========
=========2020-03-04 10:02작업 중...=========
=========2020-03-04 10:03작업 중...=========
=========2020-03-04 10:04작업 중...=========
=========2020-03-04 10:05작업 중...=========
=========2020-03-04 10:06작업 중...=========
=========2020-03-04 10:07작업 중...=========
=========2020-03-04 10:08작업 중...=========
=========2020-03-04 10:09작업 중...=========
=========2020-03-04 10:10작업 중...=========
=========2020-03-04 10:11작업 중...=========
=========2020-03-04 10:12작업 중...=========
=========2020-03-04 10:13작업 중...=========
=========2020-03-04 10:14작업 중...=========
=========2020-03-04 10:15작업 중...=========
=========2020-03-04 10:16작업 중...=========
=========2020-03-04 10:17작업 중...=========
=========2020-03-04 10:18작업 중...=========
=========2020-03-04 10:19작업 중...=========
=========2020-03-04 10:20작업 중...=========
=========2020-03-04 10:21작업 중...=========
=========2020-03-04 10:22작업 중...=========
=========2020-03-04 10:23작업 중...==

=========2020-03-04 13:16작업 중...=========
=========2020-03-04 13:17작업 중...=========
=========2020-03-04 13:18작업 중...=========
=========2020-03-04 13:19작업 중...=========
=========2020-03-04 13:20작업 중...=========
=========2020-03-04 13:21작업 중...=========
=========2020-03-04 13:22작업 중...=========
=========2020-03-04 13:23작업 중...=========
=========2020-03-04 13:24작업 중...=========
=========2020-03-04 13:25작업 중...=========
=========2020-03-04 13:26작업 중...=========
=========2020-03-04 13:27작업 중...=========
=========2020-03-04 13:28작업 중...=========
=========2020-03-04 13:29작업 중...=========
=========2020-03-04 13:30작업 중...=========
=========2020-03-04 13:31작업 중...=========
=========2020-03-04 13:32작업 중...=========
=========2020-03-04 13:33작업 중...=========
=========2020-03-04 13:34작업 중...=========
=========2020-03-04 13:35작업 중...=========
=========2020-03-04 13:36작업 중...=========
=========2020-03-04 13:37작업 중...=========
=========2020-03-04 13:38작업 중...=========
=========2020-03-04 13:39작업 중...==

...

=========2020-04-30 12:20작업 중...=========
=========2020-04-30 12:21작업 중...=========
=========2020-04-30 12:22작업 중...=========
=========2020-04-30 12:23작업 중...=========
=========2020-04-30 12:24작업 중...=========
=========2020-04-30 12:25작업 중...=========
=========2020-04-30 12:26작업 중...=========
=========2020-04-30 12:27작업 중...=========
=========2020-04-30 12:28작업 중...=========
=========2020-04-30 12:29작업 중...=========
=========2020-04-30 12:30작업 중...=========
=========2020-04-30 12:31작업 중...=========
=========2020-04-30 12:32작업 중...=========
=========2020-04-30 12:33작업 중...=========
=========2020-04-30 12:34작업 중...=========
=========2020-04-30 12:35작업 중...=========
=========2020-04-30 12:36작업 중...=========
=========2020-04-30 12:37작업 중...=========
=========2020-04-30 12:38작업 중...=========
=========2020-04-30 12:39작업 중...=========
=========2020-04-30 12:40작업 중...=========
=========2020-04-30 12:41작업 중...=========
=========2020-04-30 12:42작업 중...=========
=========2020-04-30 12:43작업 중...==

=========2020-04-30 15:36작업 중...=========
=========2020-04-30 15:37작업 중...=========
=========2020-04-30 15:38작업 중...=========
=========2020-04-30 15:39작업 중...=========
=========2020-04-30 15:40작업 중...=========
=========2020-04-30 15:41작업 중...=========
=========2020-04-30 15:42작업 중...=========
=========2020-04-30 15:43작업 중...=========
=========2020-04-30 15:44작업 중...=========
=========2020-04-30 15:45작업 중...=========
=========2020-04-30 15:46작업 중...=========
=========2020-04-30 15:47작업 중...=========
=========2020-04-30 15:48작업 중...=========
=========2020-04-30 15:49작업 중...=========
=========2020-04-30 15:50작업 중...=========
=========2020-04-30 15:51작업 중...=========
=========2020-04-30 15:52작업 중...=========
=========2020-04-30 15:53작업 중...=========
=========2020-04-30 15:54작업 중...=========
=========2020-04-30 15:55작업 중...=========
=========2020-04-30 15:56작업 중...=========
=========2020-04-30 15:57작업 중...=========
=========2020-04-30 15:58작업 중...=========
=========2020-04-30 15:59작업 중...==

=========2020-04-30 18:52작업 중...=========
=========2020-04-30 18:53작업 중...=========
=========2020-04-30 18:54작업 중...=========
=========2020-04-30 18:55작업 중...=========
=========2020-04-30 18:56작업 중...=========
=========2020-04-30 18:57작업 중...=========
=========2020-04-30 18:58작업 중...=========
=========2020-04-30 18:59작업 중...=========
=========2020-04-30 19:00작업 중...=========
=========2020-04-30 19:01작업 중...=========
=========2020-04-30 19:02작업 중...=========
=========2020-04-30 19:03작업 중...=========
=========2020-04-30 19:04작업 중...=========
=========2020-04-30 19:05작업 중...=========
=========2020-04-30 19:06작업 중...=========
=========2020-04-30 19:07작업 중...=========
=========2020-04-30 19:08작업 중...=========
=========2020-04-30 19:09작업 중...=========
=========2020-04-30 19:10작업 중...=========
=========2020-04-30 19:11작업 중...=========
=========2020-04-30 19:12작업 중...=========
=========2020-04-30 19:13작업 중...=========
=========2020-04-30 19:14작업 중...=========
=========2020-04-30 19:15작업 중...==

=========2020-04-30 22:08작업 중...=========
=========2020-04-30 22:09작업 중...=========
=========2020-04-30 22:10작업 중...=========
=========2020-04-30 22:11작업 중...=========
=========2020-04-30 22:12작업 중...=========
=========2020-04-30 22:13작업 중...=========
=========2020-04-30 22:14작업 중...=========
=========2020-04-30 22:15작업 중...=========
=========2020-04-30 22:16작업 중...=========
=========2020-04-30 22:17작업 중...=========
=========2020-04-30 22:18작업 중...=========
=========2020-04-30 22:19작업 중...=========
=========2020-04-30 22:20작업 중...=========
=========2020-04-30 22:21작업 중...=========
=========2020-04-30 22:22작업 중...=========
=========2020-04-30 22:23작업 중...=========
=========2020-04-30 22:24작업 중...=========
=========2020-04-30 22:25작업 중...=========
=========2020-04-30 22:26작업 중...=========
=========2020-04-30 22:27작업 중...=========
=========2020-04-30 22:28작업 중...=========
=========2020-04-30 22:29작업 중...=========
=========2020-04-30 22:30작업 중...=========
=========2020-04-30 22:31작업 중...==

STD_DT     NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  TAG
1       2020-03-04 0:01      14        740        1740          590  3.22    0
2       2020-03-04 0:02      24        740        1748          575  3.22    0
3       2020-03-04 0:03      34        759        1718          560  3.21    0
4       2020-03-04 0:04      44        757        1737          546  3.22    0
5       2020-03-04 0:05      54        797        1739          531  3.21    0
...                 ...     ...        ...         ...          ...   ...  ...
76314  2020-04-30 23:54  835144        784        1751          387  3.22    0
76315  2020-04-30 23:55  835154        740        1748          373  3.22    0
76316  2020-04-30 23:57  835174        728        1737          344  3.21    0
76317  2020-04-30 23:58  835184        755        1715          330  3.22    0
76318  2020-04-30 23:59  835194        749        1740          319  3.21    0

[76318 rows x 7 columns]

In [228]:
#z[(z['MOTORSPEED']>=461.3) & (z['MELT_TEMP']>=511.6) & (z['MELT_WEIGHT']>=530.2) & (z['INSP']>=3.194)]
newdata
# 

STD_DT     NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  TAG
1       2020-03-04 0:01      14        740        1740          590  3.22    0
2       2020-03-04 0:02      24        740        1748          575  3.22    0
3       2020-03-04 0:03      34        759        1718          560  3.21    0
4       2020-03-04 0:04      44        757        1737          546  3.22    0
5       2020-03-04 0:05      54        797        1739          531  3.21    0
...                 ...     ...        ...         ...          ...   ...  ...
76314  2020-04-30 23:54  835144        784        1751          387  3.22    0
76315  2020-04-30 23:55  835154        740        1748          373  3.22    0
76316  2020-04-30 23:57  835174        728        1737          344  3.21    0
76317  2020-04-30 23:58  835184        755        1715          330  3.22    0
76318  2020-04-30 23:59  835194        749        1740          319  3.21    0

[76318 rows x 7 columns]

In [229]:
newdata.to_csv('datameansample.csv')


In [231]:
newdata[newdata['STD_DT'].str.contains('2020-04-01 23:54')]

STD_DT     NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  TAG
38432  2020-04-01 23:54  417544        766        1754          821  3.21    0

In [ ]:
'''
# 10개의 데이터 (초당) 실피기 위해 각 전  # 평균보다 높은 데이터를 뽑을 수 있고 그 평균 +1 -1 범위내에서 뽑을 수 있음
def getTimeData10(data, column):
    ddf = data.loc[[0]]
    #t = timegetList(dissoul, 'STD_DT')
    for i in t:
        l = data[data[column].str.contains(i)]
        l = l[(l[l.columns[2]]>=l[l.columns[2]].mean()) & (l[l.columns[3]]>=l[l.columns[3]].mean()) 
          & (l[l.columns[4]]>=l[l.columns[4]].mean()) & (l[l.columns[5]]>=l[l.columns[5]].mean())]
        
        ddf = ddf.append(l, ignore_index = True)
        print('========='+i+'작업 중...=========')
    ddf = ddf.drop(0)
    
    return ddf
# 약간 수정을 하면
'''
# 10개의 데이터 (초당) 실피기 위해 각 전  # 평균보다 높은 데이터를 뽑을 수 있고 그 평균 +1 -1 범위내에서 뽑을 수 있음
def getTimeData10(data, column):
    ddf = data.loc[[0]]
    t = timegetList(dissoul, 'STD_DT')
    for i in t:
        l = data[data[column].str.contains(i)]
        l = l[(l[l.columns[2]]>=l[l.columns[2]].mean()) & (l[l.columns[3]]>=l[l.columns[3]].mean()) 
          & (l[l.columns[4]]>=l[l.columns[4]].mean()) & (l[l.columns[5]]>=l[l.columns[5]].mean())]
        
        # 만약 조건에 만족하는 데이터가 1개의 행도 없다면 평균값을 처리...
        if len(l) == 0:
            s = l
        ddf = ddf.append(l, ignore_index = True)
        print('========='+i+'작업 중...=========')
    ddf = ddf.drop(0)
    
    return ddf

In [ ]:
pd.DataFrame[]

In [234]:
lk = pd.DataFrame(data = , columns = dissoul.columns)

Index(['STD_DT', 'NUM', 'MELT_TEMP', 'MOTORSPEED', 'MELT_WEIGHT', 'INSP',
       'TAG'],
      dtype='object')

In [ ]:
ll = [dissoul[dissoul.columns[0]].mean(), dissoul[dissoul.columns[1]].mean(), 
      dissoul[dissoul.columns[2]].mean(), dissoul[dissoul.columns[3]].mean()]

In [ ]:
# 데이터 프레임을 array 데이터를 리스트화 시킨 후  긱 1초마다의 1개 데이터만 가져오기
def datagetTime1(data, j):
    dt = []
    
    for i in range(int(len(data)/10)):
        dt.appned(data.loc[[i*j].values])
    
    dfdata = pd.DataFrame(dt[0])
    
    for i in range(len(dt)):
        s = pd.DataFrame(dt[i])
        dfdata = dfdata.append(s, ignore_index = True)
    
    dfdata = dfdata.drop(0)
    
    return dfdata

In [17]:
# 
dissoul.loc[20]

STD_DT         2020-03-04 0:00
NUM                          9
MELT_TEMP                  489
MOTORSPEED                 148
MELT_WEIGHT                598
INSP                       3.2
TAG                          0
Name: 9, dtype: object

In [58]:
d = []
for i in range(int(len(dissoul)/10)):
    #print(dissoul.loc[i*10])
    d.append(dissoul.loc[[i*10]].values)
    

In [94]:
a = pd.DataFrame(d[0])
b = pd.DataFrame(d[1])
datadf = a.append(b, ignore_index = True)

In [97]:
a = pd.DataFrame(d[2])
b = pd.DataFrame(d[3])
datadf = datadf.append(a, ignore_index = True)

datadf

In [99]:
for i in range(len(d)):
    #a.append(i, ignore_index = True)
    #i pd.dataFrame(i)
    b = pd.DataFrame(d[i])
    datadf = datadf.append(b, ignore_index = True)

In [105]:
datadf = datadf.drop(0)
datadf = datadf.drop(1)
datadf = datadf.drop(2)

In [116]:
datadf = datadf.reset_index(drop=True)
#datadf.rename()
datadf[datadf[6] == 1] # 각 시간대별로 가장 마지막 10중 1개의 데이터를 선별

0       1    2    3     4     5  6
21791   2020-03-19 3:11  217910  414  124   367   3.2  1
22201  2020-03-19 10:01  222010  453  135   180  3.19  1
22289  2020-03-19 11:29  222890  452  129  1621   3.2  1
22292  2020-03-19 11:32  222920  449  112  1579  3.19  1
22316  2020-03-19 11:56  223160  455  117  1250  3.19  1
...                 ...     ...  ...  ...   ...   ... ..
59803  2020-04-14 12:43  598030  452  120   340  3.19  1
59814  2020-04-14 12:54  598140  457  108   175  3.19  1
59823  2020-04-14 13:03  598230  450  120    38   3.2  1
59825  2020-04-14 13:05  598250  458  113    11  3.19  1
59832  2020-04-14 13:12  598320  448  158   315   3.2  1

[12598 rows x 7 columns]

In [119]:
datadf[datadf[6] == 0]

0       1    2    3    4     5  6
0       2020-03-04 0:00       0  489  116  631  3.19  0
1       2020-03-04 0:01      10  507  128  596  3.19  0
2       2020-03-04 0:02      20  474  135  581  3.19  0
3       2020-03-04 0:03      30  437  129  567  3.19  0
4       2020-03-04 0:04      40  450  145  552  3.19  0
...                 ...     ...  ...  ...  ...   ... ..
83515  2020-04-30 23:55  835150  470  136  379  3.19  0
83516  2020-04-30 23:56  835160  496  103  362   3.2  0
83517  2020-04-30 23:57  835170  465  108  348  3.19  0
83518  2020-04-30 23:58  835180  498  133  335  3.19  0
83519  2020-04-30 23:59  835190  497  141  323   3.2  0

[70922 rows x 7 columns]

In [117]:
# copy 
datadfcopy = datadf.copy()

In [181]:
datadfcopy # 데이터프레임 각 1초당 맨 앞자리 데이터 추출 새로운 데이터 프레임 추출

0       1    2    3    4     5  6
0       2020-03-04 0:00       0  489  116  631  3.19  0
1       2020-03-04 0:01      10  507  128  596  3.19  0
2       2020-03-04 0:02      20  474  135  581  3.19  0
3       2020-03-04 0:03      30  437  129  567  3.19  0
4       2020-03-04 0:04      40  450  145  552  3.19  0
...                 ...     ...  ...  ...  ...   ... ..
83515  2020-04-30 23:55  835150  470  136  379  3.19  0
83516  2020-04-30 23:56  835160  496  103  362   3.2  0
83517  2020-04-30 23:57  835170  465  108  348  3.19  0
83518  2020-04-30 23:58  835180  498  133  335  3.19  0
83519  2020-04-30 23:59  835190  497  141  323   3.2  0

[83520 rows x 7 columns]

In [182]:
datadfcopy.to_csv('dissoulsample.csv')

In [118]:
sign = lambda x: (1, -1)[x < 0]

def curve_shift(data, target, shiftby):
    vector = data[target].copy()
    
    for i in range(abs(shiftby)):
        temp = vector.shift(sign(shiftby))
        temp = temp.fillna(0)
        vector += temp
    
    label = target
    
    data.insert(loc = 0, column = label + 'temp', value = vector)
    
    data = data.drop(data[data[label] == 1].index)
    #
    data = data.drop(label, axis = 1)
    data = data.rename(columns = {label + 'temp' : label})
    
    data.loc[data[label] > 0, label ] = 1
    
    return data

In [ ]:
shifted_cessing_df = curve_shift(datadfcopy, 6, shiftby=-2) # 데이터를 10개 중 1개씩 (1초당 1개 데이터) ->ㅣ 
shifted_cessing_df.head()

In [81]:
d[0]

array([['2020-03-04 0:00', 0, 489, 116, 631, 3.19, 0]], dtype=object)

In [46]:
list(dissoul.loc[[333000]].values)

[array(['2020-03-27 3:00', 333000, 502, 133, 729, 3.19, 1], dtype=object)]

In [ ]:
# 1초마다 데이터가 10개이면 - 각 초마다 데이터를 1개씩 뽑아야 할까요? - 왜냐하면 step 수가 너무 많아지면 정확한 이상탐지 하기 어려울 판단됨
# 각 초마다의 데이터의 이상 데이터를 뽑아 내는 방법이 잇음


In [11]:
dissoul[dissoul['TAG'] == 1]

STD_DT     NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  \
188733   2020-03-17 2:33  188733        338         202          205  3.18   
188823   2020-03-17 2:42  188823        364         201           66  3.18   
188826   2020-03-17 2:42  188826        362         203           61  3.19   
188896   2020-03-17 2:49  188896        370         206          112  3.18   
188903   2020-03-17 2:50  188903        365         238          151  3.19   
...                  ...     ...        ...         ...          ...   ...   
598507  2020-04-14 13:30  598507        454         178          344  3.19   
598551  2020-04-14 13:35  598551        458          73          269  3.19   
598567  2020-04-14 13:36  598567        452         156          236  3.19   
598597  2020-04-14 13:39  598597        455         160          177  3.19   
598598  2020-04-14 13:39  598598        457          82          176  3.19   

        TAG  
188733    1  
188823    1  
188826    1  
188896    1  
188903    1  
...     ...  
598507    1  
598551    1  
598567    1  
598597    1  
598598    1  

[177067 rows x 7 columns]

In [12]:
dissoul[dissoul['STD_DT'].str.contains('2020-03-04')] # EDA 각 날짜별로 NG 데이터 개수는 ???

STD_DT    NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  TAG
0       2020-03-04 0:00      0        489         116          631  3.19    0
1       2020-03-04 0:00      1        433          78          609  3.19    0
2       2020-03-04 0:00      2        464         154          608  3.19    0
3       2020-03-04 0:00      3        379         212          606  3.19    0
4       2020-03-04 0:00      4        798        1736          604  3.21    0
...                 ...    ...        ...         ...          ...   ...  ...
14395  2020-03-04 23:59  14395        752        1745          188  3.21    0
14396  2020-03-04 23:59  14396        423         205          187  3.18    0
14397  2020-03-04 23:59  14397        483         182          185  3.19    0
14398  2020-03-04 23:59  14398        430          94          184  3.19    0
14399  2020-03-04 23:59  14399        502         108          183  3.19    0

[14400 rows x 7 columns]

In [72]:
'''
def date_find(str(i), str(j)):
    i, j = input("날짜를 입력하시오", i, j)
    
    d_i_j = dissoul[dissoul['STD_DT'].str.contains('2020-03-04')]

'''

SyntaxError: invalid syntax (3053568809.py, line 1)

In [13]:
#for i in range(9):
#   d_3_i = dissoul[dissoul['STD_DT'].str.contains('2020-'+'03-0'+str(i))]
    
    #print(d_3_i)
    

d_3_4 = dissoul[dissoul['STD_DT'].str.contains('2020-03-04')]
d_3_5 = dissoul[dissoul['STD_DT'].str.contains('2020-03-05')]
d_3_6 = dissoul[dissoul['STD_DT'].str.contains('2020-03-06')]
d_3_7 = dissoul[dissoul['STD_DT'].str.contains('2020-03-07')]
d_3_8 = dissoul[dissoul['STD_DT'].str.contains('2020-03-08')]
d_3_9 = dissoul[dissoul['STD_DT'].str.contains('2020-03-09')]
d_3_10 = dissoul[dissoul['STD_DT'].str.contains('2020-03-10')]   
d_3_11 = dissoul[dissoul['STD_DT'].str.contains('2020-03-11')]
d_3_12 = dissoul[dissoul['STD_DT'].str.contains('2020-03-12')]
d_3_13 = dissoul[dissoul['STD_DT'].str.contains('2020-03-13')]
d_3_14 = dissoul[dissoul['STD_DT'].str.contains('2020-03-14')]
d_3_15 = dissoul[dissoul['STD_DT'].str.contains('2020-03-15')]
d_3_16 = dissoul[dissoul['STD_DT'].str.contains('2020-03-16')]
d_3_17 = dissoul[dissoul['STD_DT'].str.contains('2020-03-17')]
d_3_18 = dissoul[dissoul['STD_DT'].str.contains('2020-03-18')]
d_3_19 = dissoul[dissoul['STD_DT'].str.contains('2020-03-19')]
d_3_20 = dissoul[dissoul['STD_DT'].str.contains('2020-03-20')]
d_3_21 = dissoul[dissoul['STD_DT'].str.contains('2020-03-21')]
d_3_22 = dissoul[dissoul['STD_DT'].str.contains('2020-03-22')]
d_3_23 = dissoul[dissoul['STD_DT'].str.contains('2020-03-23')]
d_3_24 = dissoul[dissoul['STD_DT'].str.contains('2020-03-24')]
d_3_25 = dissoul[dissoul['STD_DT'].str.contains('2020-03-25')]
d_3_26 = dissoul[dissoul['STD_DT'].str.contains('2020-03-26')]
d_3_27 = dissoul[dissoul['STD_DT'].str.contains('2020-03-27')]
d_3_28 = dissoul[dissoul['STD_DT'].str.contains('2020-03-28')]
d_3_29 = dissoul[dissoul['STD_DT'].str.contains('2020-03-29')]
d_3_30 = dissoul[dissoul['STD_DT'].str.contains('2020-03-30')]
d_3_31 = dissoul[dissoul['STD_DT'].str.contains('2020-03-31')]



d_4_1 = dissoul[dissoul['STD_DT'].str.contains('2020-04-01')]
d_4_2 = dissoul[dissoul['STD_DT'].str.contains('2020-04-02')]
d_4_3 = dissoul[dissoul['STD_DT'].str.contains('2020-04-03')]
d_4_4 = dissoul[dissoul['STD_DT'].str.contains('2020-04-04')]
d_4_5 = dissoul[dissoul['STD_DT'].str.contains('2020-04-05')]
d_4_6 = dissoul[dissoul['STD_DT'].str.contains('2020-04-06')]
d_4_7 = dissoul[dissoul['STD_DT'].str.contains('2020-04-07')]
d_4_8 = dissoul[dissoul['STD_DT'].str.contains('2020-04-08')]
d_4_9 = dissoul[dissoul['STD_DT'].str.contains('2020-04-09')]
d_4_10 = dissoul[dissoul['STD_DT'].str.contains('2020-04-10')]
d_4_11 = dissoul[dissoul['STD_DT'].str.contains('2020-04-11')]
d_4_12 = dissoul[dissoul['STD_DT'].str.contains('2020-04-12')]
d_4_13 = dissoul[dissoul['STD_DT'].str.contains('2020-04-13')]
d_4_14 = dissoul[dissoul['STD_DT'].str.contains('2020-04-14')]
d_4_15 = dissoul[dissoul['STD_DT'].str.contains('2020-04-15')]
d_4_16 = dissoul[dissoul['STD_DT'].str.contains('2020-04-16')]
d_4_17 = dissoul[dissoul['STD_DT'].str.contains('2020-04-17')]
d_4_18 = dissoul[dissoul['STD_DT'].str.contains('2020-04-18')]
d_4_19 = dissoul[dissoul['STD_DT'].str.contains('2020-04-19')]
d_4_20 = dissoul[dissoul['STD_DT'].str.contains('2020-04-20')]
d_4_21 = dissoul[dissoul['STD_DT'].str.contains('2020-04-21')]
d_4_22 = dissoul[dissoul['STD_DT'].str.contains('2020-04-22')]
d_4_23 = dissoul[dissoul['STD_DT'].str.contains('2020-04-23')]
d_4_24 = dissoul[dissoul['STD_DT'].str.contains('2020-04-24')]
d_4_25 = dissoul[dissoul['STD_DT'].str.contains('2020-04-25')]
d_4_26 = dissoul[dissoul['STD_DT'].str.contains('2020-04-26')]
d_4_27 = dissoul[dissoul['STD_DT'].str.contains('2020-04-27')]
d_4_28 = dissoul[dissoul['STD_DT'].str.contains('2020-04-28')]
d_4_29 = dissoul[dissoul['STD_DT'].str.contains('2020-04-29')]
d_4_30 = dissoul[dissoul['STD_DT'].str.contains('2020-04-30')]



In [ ]:
# 그러니까 결국 1초당 9개 데이터를 모두 학습을 통해 특징을 추출하고 그것을 바탕으로 shift하는게 맞지 않을까 라는 생각이 든다.
# 3600초는 1시간 - 9 * 3600
# 1일 - 3600 * 24  = *9 데이터가 커지지 않을까? 생각해서 고안했습니다. 특징

In [14]:
#d_4_18[d_4_18['TAG'] == 1]  #4/15 ~ 4/30까지 OK, 3/04 ~ 3/16까지 OK
d_3_28  # 3/17~ 4/15까지 NG가 있고

STD_DT     NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  \
345600   2020-03-28 0:00  345600        470         130          757  3.19   
345601   2020-03-28 0:00  345601        422          86          758  3.19   
345602   2020-03-28 0:00  345602        468         146          758  3.19   
345603   2020-03-28 0:00  345603        409         236         7578  3.18   
345604   2020-03-28 0:00  345604        786        1750          758  3.21   
...                  ...     ...        ...         ...          ...   ...   
359995  2020-03-28 23:59  359995        754        1739          127  3.21   
359996  2020-03-28 23:59  359996        376         220          133  3.19   
359997  2020-03-28 23:59  359997        459         166          138  3.19   
359998  2020-03-28 23:59  359998        429          75          143  3.19   
359999  2020-03-28 23:59  359999        470          98          148  3.19   

        TAG  
345600    1  
345601    1  
345602    1  
345603    1  
345604    0  
...     ...  
359995    0  
359996    1  
359997    1  
359998    1  
359999    1  

[14400 rows x 7 columns]

In [51]:
dissoul[dissoul['STD_DT'].str.contains('2020-03-17')]


STD_DT     NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP  \
187200   2020-03-17 0:00  187200        507         116           11  3.18   
187201   2020-03-17 0:00  187201        427          70           10  3.19   
187202   2020-03-17 0:00  187202        494         166            9  3.19   
187203   2020-03-17 0:00  187203        385         211            8  3.19   
187204   2020-03-17 0:00  187204        791        1750            7  3.22   
...                  ...     ...        ...         ...          ...   ...   
201595  2020-03-17 23:59  201595        775        1738          401  3.22   
201596  2020-03-17 23:59  201596        406         214          400  3.19   
201597  2020-03-17 23:59  201597        467         178          398  3.19   
201598  2020-03-17 23:59  201598        431           0          397  3.19   
201599  2020-03-17 23:59  201599        484         112          395  3.19   

        TAG  
187200    0  
187201    0  
187202    0  
187203    0  
187204    0  
...     ...  
201595    0  
201596    1  
201597    0  
201598    0  
201599    0  

[14400 rows x 7 columns]

In [15]:
sign = lambda x: (1, -1)[x < 0]

def curve_shift(data, target, shiftby):
    vector = data[target].copy()
    
    for i in range(abs(shiftby)):
        temp = vector.shift(sign(shiftby))
        temp = temp.fillna(0)
        vector += temp
    
    label = target
    
    data.insert(loc = 0, column = label + 'temp', value = vector)
    
    data = data.drop(data[data[label] == 1].index)
    #
    data = data.drop(label, axis = 1)
    data = data.rename(columns = {label + 'temp' : label})
    
    data.loc[data[label] > 0, label ] = 1
    
    return data


In [16]:
shifted_df = curve_shift(dissoul, 'TAG', shiftby=-36001) # 600(1분당 10개 데이터 * 60 = 1시간)* 24 = 14400 하루 
shifted_df.head()


TAG           STD_DT  NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  INSP
0  0.0  2020-03-04 0:00    0        489         116          631  3.19
1  0.0  2020-03-04 0:00    1        433          78          609  3.19
2  0.0  2020-03-04 0:00    2        464         154          608  3.19
3  0.0  2020-03-04 0:00    3        379         212          606  3.19
4  0.0  2020-03-04 0:00    4        798        1736          604  3.21

In [17]:
shifted_df.shape

(658133, 7)

In [35]:
shifted_df[shifted_df['TAG'] == 1].head()

TAG            STD_DT     NUM  MELT_TEMP  MOTORSPEED  MELT_WEIGHT  \
152732  1.0  2020-03-14 14:33  152732        472         178           68   
152733  1.0  2020-03-14 14:33  152733        405         220           67   
152734  1.0  2020-03-14 14:33  152734        759        1736           65   
152735  1.0  2020-03-14 14:33  152735        757        1731           63   
152736  1.0  2020-03-14 14:33  152736        369         188           62   

        INSP  
152732  3.20  
152733  3.19  
152734  3.22  
152735  3.22  
152736  3.18

In [44]:

inputx = shifted_df[['MELT_TEMP', 'MOTORSPEED', 'MELT_WEIGHT', 'INSP', 'TAG']]
inputy = shifted_df[['TAG']]

# x, y
inputx = inputx.values
inputy = inputy.values

n_features = inputx.shape[1]

In [46]:
def transformlization(x, y, timestep):
    x_outdata = []
    y_outdata = []
    
    timestep = 10*timestep
    
    for i in range(len(x) - timestep -1):
        t_list = []
        
        for j in range(1, timestep + 1):
            t_list.append(x[[(i+j+1)], :])
            
        x_outdata.append(t_list)
        y_outdata.append(y[i+ timestep + 1])
    
        

    sq = np.squeeze(np.array(x_outdata))
    yd = np.array(y_output)
    return sq, yd

In [ ]:
timestep = 60 #60*24 #
#
datax, datay = transformlization(inputx, inputy, timestep) 


In [ ]:
datax.shape

In [ ]:
trainx, testx, trainy, testy = train_test_split(datax, datay, test_size = 0.3)


In [ ]:
# Split into train, valid, and test 
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.2)
x_train, x_valid, y_train, y_valid = train_test_split(x_train, y_train, test_size=0.2)

print(len(x_train))  # 11691
print(len(x_valid))  # 2923
print(len(x_test))   # 3654

In [103]:
ddf = ddfnew.copy()

In [106]:
ddf = ddf.drop('Unnamed: 0', axis = 1)